#Instalações/importações


In [40]:
%pip install ydata_profiling


In [41]:
import yfinance as yf
import pandas as pd
import numpy as np
from ydata_profiling import ProfileReport
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM,GRU, Dropout, Dense
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

#Exploração dos dados


##importando dados das criptomoedas que serão trabalhadas utilizando o yfinance. Aqui utilizarei o Bitcoin e a Ethereum


In [42]:
#bitcoin
btc = yf.Ticker("BTC-USD")
btc_hist = btc.history(period="max")
btc_hist = btc_hist.reset_index()

In [43]:
#ethereum
eth = yf.Ticker("ETH-USD")
eth_hist = eth.history(period="max")
eth_hist = eth_hist.reset_index()

##exploração bitcoin


In [44]:
btc_hist.head()

Date        Open        High         Low       Close  \
0 2014-09-17 00:00:00+00:00  465.864014  468.174011  452.421997  457.334015   
1 2014-09-18 00:00:00+00:00  456.859985  456.859985  413.104004  424.440002   
2 2014-09-19 00:00:00+00:00  424.102997  427.834991  384.532013  394.795990   
3 2014-09-20 00:00:00+00:00  394.673004  423.295990  389.882996  408.903992   
4 2014-09-21 00:00:00+00:00  408.084991  412.425995  393.181000  398.821014   

     Volume  Dividends  Stock Splits  
0  21056800        0.0           0.0  
1  34483200        0.0           0.0  
2  37919700        0.0           0.0  
3  36863600        0.0           0.0  
4  26580100        0.0           0.0

In [45]:
btc_hist.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3660 entries, 0 to 3659
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype              
---  ------        --------------  -----              
 0   Date          3660 non-null   datetime64[ns, UTC]
 1   Open          3660 non-null   float64            
 2   High          3660 non-null   float64            
 3   Low           3660 non-null   float64            
 4   Close         3660 non-null   float64            
 5   Volume        3660 non-null   int64              
 6   Dividends     3660 non-null   float64            
 7   Stock Splits  3660 non-null   float64            
dtypes: datetime64[ns, UTC](1), float64(6), int64(1)
memory usage: 228.9 KB


In [46]:
btc_hist.shape

(3660, 8)

In [47]:
# aprentementente as colunas "dividens" e "stock splits" não apresentam valores
# diferentes de zero. Portanto, iremos conferir se essa hpótese é verdadeira e,
# com isso, podemos tomar melhores decisões em relação a essas colunas no
# tratamento dos dados.

valores_dividends= btc_hist["Dividends"].unique()
valores_stocksplits = btc_hist["Stock Splits"].unique()
print(valores_dividends)
print(valores_stocksplits)

# com isso podemos confirmar a hipótese dada inicialmente

[0.]
[0.]


In [48]:
# Realizando a análise
profile = ProfileReport(btc_hist, title="Pandas Profiling Report")
# Exibindo os resultados
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**Conclusões em relação à exploração dos dados:**
- não há dados faltantes no dataset
- todas as colunas apresentam dados numéricos
- as colunas "dividends" e "stock splits" apresentam apenas um valor, "0"
- contamos com 3659 linhas (registros)
- as colunas apresentam alta taxa de correlação em nível diretamente proporcional

**Significado de cada coluna:**
- Date: A data correspondente ao período da linha. Representa o dia específico em que os dados de preços e volume foram registrados.
- Open: O preço de abertura da criptomoeda no início do período (geralmente, um dia). Isso representa o preço ao qual a primeira negociação foi realizada naquele dia.
- High: O preço mais alto ao qual a criptomoeda foi negociada durante o período. É o valor máximo alcançado entre a abertura e o fechamento do mercado.
- Low: O preço mais baixo ao qual a criptomoeda foi negociada durante o período. Representa o valor mínimo registrado ao longo do dia.
- Close: O preço de fechamento da criptomoeda no final do período (geralmente, o fim do dia). Esse é o preço da última negociação realizada antes do encerramento do mercado.
- Volume: O volume de negociação durante o período. Indica a quantidade de unidades da criptomoeda que foram compradas e vendidas no intervalo considerado. Um volume maior geralmente significa que houve mais atividade no mercado.
- Dividends: No dataset, essa coluna mostra os valores de dividendos pagos por ação em determinadas datas. Se uma empresa pagou dividendos, o valor aparecerá nessa coluna correspondente à data em que o dividendo foi pago.
- Stock Splits: Essa coluna registra quando e como ocorreram os desdobramentos de ações. Os valores indicam a proporção do desdobramento.

**Insights:**

- no tratamento dos dados, não será necessário lidar com dados nulos
- também no tratamento dos dados, é possível excluir as colunas dividends e stock split, uma vez que por padrão essa coluna sempre será nula.
- a correlação das colunas sempre será alta, uma vez que, pelos seus significados, os valores sempre serão muito próximos. Esse fato pode gerar redundancia, logo, irei testar o modelo com todas as colunas e sem todas elas, mantendo apenas uma representativa, para ver a performance do modelo.

## exploração ethereum

In [49]:
eth_hist.head()

Date        Open        High         Low       Close  \
0 2017-11-09 00:00:00+00:00  308.644989  329.451996  307.056000  320.884003   
1 2017-11-10 00:00:00+00:00  320.670990  324.717987  294.541992  299.252991   
2 2017-11-11 00:00:00+00:00  298.585999  319.453003  298.191986  314.681000   
3 2017-11-12 00:00:00+00:00  314.690002  319.153015  298.513000  307.907990   
4 2017-11-13 00:00:00+00:00  307.024994  328.415009  307.024994  316.716003   

       Volume  Dividends  Stock Splits  
0   893249984        0.0           0.0  
1   885985984        0.0           0.0  
2   842300992        0.0           0.0  
3  1613479936        0.0           0.0  
4  1041889984        0.0           0.0

In [50]:
eth_hist.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2511 entries, 0 to 2510
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype              
---  ------        --------------  -----              
 0   Date          2511 non-null   datetime64[ns, UTC]
 1   Open          2511 non-null   float64            
 2   High          2511 non-null   float64            
 3   Low           2511 non-null   float64            
 4   Close         2511 non-null   float64            
 5   Volume        2511 non-null   int64              
 6   Dividends     2511 non-null   float64            
 7   Stock Splits  2511 non-null   float64            
dtypes: datetime64[ns, UTC](1), float64(6), int64(1)
memory usage: 157.1 KB


In [51]:
eth_hist.shape

(2511, 8)

In [52]:
# aprentementente as colunas "dividens" e "stock splits" não apresentam valores
# diferentes de zero. Portanto, iremos conferir se essa hpótese é verdadeira e,
# com isso, podemos tomar melhores decisões em relação a essas colunas no
# tratamento dos dados.

valores_dividends= eth_hist["Dividends"].unique()
valores_stocksplits = eth_hist["Stock Splits"].unique()
print(valores_dividends)
print(valores_stocksplits)

# com isso podemos confirmar a hipótese dada inicialmente

[0.]
[0.]


In [53]:
# Realizando a análise
profile = ProfileReport(eth_hist, title="Pandas Profiling Report")
# Exibindo os resultados
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**Conclusões em relação à exploração dos dados:**
- não há dados faltantes no dataset
- todas as colunas apresentam dados numéricos
- as colunas "dividends" e "stock splits" apresentam apenas um valor, "0"
- contamos com 2510 linhas (registros)
- as colunas "low", "high", "open" e "close" apresentam alta taxa de correlação em nível diretamente proporcional

**Significado de cada coluna:**
- Date: A data correspondente ao período da linha. Representa o dia específico em que os dados de preços e volume foram registrados.
- Open: O preço de abertura da criptomoeda no início do período (geralmente, um dia). Isso representa o preço ao qual a primeira negociação foi realizada naquele dia.
- High: O preço mais alto ao qual a criptomoeda foi negociada durante o período. É o valor máximo alcançado entre a abertura e o fechamento do mercado.
- Low: O preço mais baixo ao qual a criptomoeda foi negociada durante o período. Representa o valor mínimo registrado ao longo do dia.
- Close: O preço de fechamento da criptomoeda no final do período (geralmente, o fim do dia). Esse é o preço da última negociação realizada antes do encerramento do mercado.
- Volume: O volume de negociação durante o período. Indica a quantidade de unidades da criptomoeda que foram compradas e vendidas no intervalo considerado. Um volume maior geralmente significa que houve mais atividade no mercado.
- Dividends: No dataset, essa coluna mostra os valores de dividendos pagos por ação em determinadas datas. Se uma empresa pagou dividendos, o valor aparecerá nessa coluna correspondente à data em que o dividendo foi pago.
- Stock Splits: Essa coluna registra quando e como ocorreram os desdobramentos de ações. Os valores indicam a proporção do desdobramento.

**Insights:**

- no tratamento dos dados, não será necessário lidar com dados nulos
- também no tratamento dos dados, é possível excluir as colunas dividends e stock split, uma vez que por padrão essa coluna sempre será nula.
- a correlação das colunas mencionadas anteriormente sempre será alta, uma vez que, pelos seus significados, os valores sempre serão muito próximos. Esse fato pode gerar redundancia, logo, irei testar o modelo deixando apenas uma coluna representativa das quatro colunas com alto grau de relação, além do target ('Close).

# Tratamento de dados

In [54]:
# excluindo colunas "Dividends" e "Stock Splits"
btc = btc_hist.drop(columns=["Dividends", "Stock Splits"])
eth = eth_hist.drop(columns=["Dividends", "Stock Splits"])

In [55]:
# Converter a coluna Date para o tipo datetime, se ainda não estiver
btc['Date'] = pd.to_datetime(btc['Date'])

# Extrair componentes da data
btc['Year'] = btc['Date'].dt.year
btc['Month'] = btc['Date'].dt.month
btc['Day'] = btc['Date'].dt.day
btc['Weekday'] = btc['Date'].dt.weekday  # Segunda-feira = 0, Domingo = 6
btc['DayOfYear'] = btc['Date'].dt.dayofyear
btc['Quarter'] = btc['Date'].dt.quarter

# Agora você pode excluir a coluna original 'Date', se desejar
btc = btc.drop(columns=['Date'])

# Converter a coluna Date para o tipo datetime, se ainda não estiver
eth['Date'] = pd.to_datetime(eth['Date'])

# Extrair componentes da data
eth['Year'] = eth['Date'].dt.year
eth['Month'] = eth['Date'].dt.month
eth['Day'] = eth['Date'].dt.day
eth['Weekday'] = eth['Date'].dt.weekday  # Segunda-feira = 0, Domingo = 6
eth['DayOfYear'] = eth['Date'].dt.dayofyear
eth['Quarter'] = eth['Date'].dt.quarter

# Agora você pode excluir a coluna original 'Date', se desejar
eth = eth.drop(columns=['Date'])

print(btc.head())
print(eth.head())


         Open        High         Low       Close    Volume  Year  Month  Day  \
0  465.864014  468.174011  452.421997  457.334015  21056800  2014      9   17   
1  456.859985  456.859985  413.104004  424.440002  34483200  2014      9   18   
2  424.102997  427.834991  384.532013  394.795990  37919700  2014      9   19   
3  394.673004  423.295990  389.882996  408.903992  36863600  2014      9   20   
4  408.084991  412.425995  393.181000  398.821014  26580100  2014      9   21   

   Weekday  DayOfYear  Quarter  
0        2        260        3  
1        3        261        3  
2        4        262        3  
3        5        263        3  
4        6        264        3  
         Open        High         Low       Close      Volume  Year  Month  \
0  308.644989  329.451996  307.056000  320.884003   893249984  2017     11   
1  320.670990  324.717987  294.541992  299.252991   885985984  2017     11   
2  298.585999  319.453003  298.191986  314.681000   842300992  2017     11   
3  

In [56]:
# normalizando dados
scaler = MinMaxScaler()

# Normalizar todas as colunas
btc = pd.DataFrame(scaler.fit_transform(btc), columns=btc.columns)
eth = pd.DataFrame(scaler.fit_transform(eth), columns=eth.columns)

print(btc)
print(eth)

          Open      High       Low     Close    Volume  Year     Month  \
0     0.003964  0.003487  0.003947  0.003830  0.000043   0.0  0.727273   
1     0.003840  0.003333  0.003395  0.003379  0.000081   0.0  0.727273   
2     0.003391  0.002939  0.002993  0.002972  0.000091   0.0  0.727273   
3     0.002987  0.002877  0.003069  0.003166  0.000088   0.0  0.727273   
4     0.003171  0.002729  0.003115  0.003027  0.000059   0.0  0.727273   
...        ...       ...       ...       ...       ...   ...       ...   
3655  0.843240  0.865681  0.863352  0.860874  0.121678   1.0  0.727273   
3656  0.860938  0.869041  0.873958  0.864338  0.100214   1.0  0.727273   
3657  0.864270  0.861206  0.879839  0.867106  0.041038   1.0  0.727273   
3658  0.867185  0.867326  0.875027  0.870589  0.057492   1.0  0.727273   
3659  0.870166  0.876413  0.881067  0.868463  0.089296   1.0  0.727273   

           Day   Weekday  DayOfYear   Quarter  
0     0.533333  0.333333   0.709589  0.666667  
1     0.566667 

# Teste de modelos

## BTC


In [67]:
# Separando as features (X) e o target (y)
X = btc.drop(columns=['Close', 'High', 'Low', 'Open'])  # 'KNR' é apenas um identificador, então deve ser removido
y = btc['Close']

In [68]:
# Separando em dados de treino e teste
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [69]:
# Converte X_train e X_test para arrays NumPy, caso ainda não sejam.
X_train = np.array(X_train)
X_test = np.array(X_test)

# Reestrutura X_train e X_test para ter 3 dimensões.
# A nova forma do array será (n_samples, n_features, 1)
X_train = X_train.reshape((X_train.shape[0], X_train.shape[1], 1))
X_test = X_test.reshape((X_test.shape[0], X_test.shape[1], 1))

In [70]:
# Construção do modelo com LSTM
model = Sequential()

model.add(LSTM(50, activation='relu', return_sequences=True, input_shape=(X_train.shape[1], 1)))
model.add(LSTM(50, activation='relu'))
model.add(Dense(1))

model.compile(optimizer='adam', loss='mse')

/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


In [71]:
# Treinamento do modelo
model.fit(X_train, y_train, epochs=100, batch_size=32, validation_data=(X_test, y_test))

Epoch 1/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 4s 14ms/step - loss: 0.1018 - val_loss: 0.0587
Epoch 2/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - loss: 0.0533 - val_loss: 0.0337
Epoch 3/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - loss: 0.0236 - val_loss: 0.0258
Epoch 4/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - loss: 0.0200 - val_loss: 0.0261
Epoch 5/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - loss: 0.0206 - val_loss: 0.0259
Epoch 6/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 2s 16ms/step - loss: 0.0182 - val_loss: 0.0291
Epoch 7/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 2s 9ms/step - loss: 0.0207 - val_loss: 0.0303
Epoch 8/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - loss: 0.0196 - val_loss: 0.0286
Epoch 9/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - loss: 0.0182 - val_loss: 0.0260
Epoch 10/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - loss: 0.0189 - val_loss: 0.0279
Epoch 11/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - loss: 0.0181 - val_loss: 0.0281
Epoch 12/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - loss:

In [72]:
# Prever os dados de teste
y_pred = model.predict(X_test)

# Calcular as métricas de regressão
mse = mean_squared_error(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print(f'MSE: {mse}')
print(f'MAE: {mae}')
print(f'R²: {r2}')

23/23 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step
MSE: 0.04057161472135527
MAE: 0.0396571375029215
R²: 0.425018028468625


In [63]:
# Construção do modelo com GRU
model_2 = Sequential()

model_2.add(GRU(50, activation='relu', return_sequences=True, input_shape=(X_train.shape[1], 1)))
model_2.add(GRU(50, activation='relu'))
model_2.add(Dense(1, activation='sigmoid'))

model_2.compile(optimizer='adam', loss='binary_crossentropy')

/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


In [64]:
# Treinamento do modelo
model_2.fit(X_train, y_train, epochs=100, batch_size=32, validation_data=(X_test, y_test))

Epoch 1/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 6s 17ms/step - loss: 0.6215 - val_loss: 0.5318
Epoch 2/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - loss: 0.5328 - val_loss: 0.3422
Epoch 3/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - loss: 0.3561 - val_loss: 0.3332
Epoch 4/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - loss: 0.3541 - val_loss: 0.3299
Epoch 5/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 2s 18ms/step - loss: 0.3583 - val_loss: 0.3286
Epoch 6/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 2s 21ms/step - loss: 0.3600 - val_loss: 0.3276
Epoch 7/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - loss: 0.3580 - val_loss: 0.3273
Epoch 8/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 2s 12ms/step - loss: 0.3534 - val_loss: 0.3275
Epoch 9/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - loss: 0.3523 - val_loss: 0.3279
Epoch 10/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - loss: 0.3559 - val_loss: 0.3267
Epoch 11/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - loss: 0.3578 - val_loss: 0.3266
Epoch 12/100
92/92 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step

In [65]:
# Prever os dados de teste
y_pred_2 = model_2.predict(X_test)
# Calcular as métricas de regressão
mse = mean_squared_error(y_test, y_pred_2)
mae = mean_absolute_error(y_test, y_pred_2)
r2 = r2_score(y_test, y_pred_2)

print(f'MSE: {mse}')
print(f'MAE: {mae}')
print(f'R²: {r2}')

23/23 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step
MSE: 0.00015548498124254775
MAE: 0.006765212971367362
R²: 0.9977964628306671


##ETH


In [66]:
# Separando as features (X) e o target (y)
X = btc.drop(columns=['Close'])  # 'KNR' é apenas um identificador, então deve ser removido
y = btc['Close']